In [146]:
import psycopg2
import pandas as pd
import numpy as np
import plotly.graph_objects as go
import plotly.offline as plot
import plotly.io as pio
import plotly.express as px
from plotly.subplots import make_subplots


In [147]:
conn = psycopg2.connect(
           dbname="qdap_test",
           user="amt",
           password="your_password",
           host="192.168.2.23",
           port="5432"
       )

# Create a cursor object using the cursor() method
cursor = conn.cursor()

def fetch_options(cursor, symbol, expiry):
    query = '''
        SELECT * 
        FROM ohlcv_options_per_minute oopm
        WHERE symbol = %s
        AND expiry_type = 'I'
        AND expiry = %s
        ORDER BY date_timestamp;
        '''
    cursor.execute(query,(symbol,expiry))
    rows = cursor.fetchall()
    df = pd.DataFrame(rows, columns=[desc[0] for desc in cursor.description])
    return df
# Create a cursor object
cursor = conn.cursor()

def fetch_futures(cursor, symbol, x):
    query = '''
        SELECT *
        FROM ohlcv_future_per_minute ofpm 
        WHERE ofpm.symbol = %s
        AND ofpm.expiry_type = 'I'
        AND DATE(ofpm.expiry) = %s
        ORDER BY date_timestamp ASC
    '''
    # Execute the query with parameters as a tuple
    cursor.execute(query, (symbol, x))
    rows = cursor.fetchall()
    df = pd.DataFrame(rows, columns=[desc[0] for desc in cursor.description])
    return df

# Define the fetch_expiries function
def fetch_expiries(cursor, symbol):
    query = f'''
        SELECT DISTINCT ofpem.expiry 
        FROM ohlcv_future_per_minute ofpem 
        WHERE ofpem.symbol = '{symbol}'
        AND ofpem.expiry_type = 'I'
        GROUP BY ofpem.expiry 
    '''
    cursor.execute(query)
    rows = cursor.fetchall()
    df = pd.DataFrame(rows, columns=[desc[0] for desc in cursor.description])
    return df

In [148]:
symbol = 'BANKNIFTY'  # Replace with your symbol
expiry_future = fetch_expiries(cursor, symbol)

# Convert the 'expiry' column to datetime and then to date
expiry_future['expiry'] = pd.to_datetime(expiry_future['expiry']).dt.date

# Print the expiry dates with their indices
for i, row in expiry_future.iterrows():
    print(i, row.iloc[0], sep=' = ', end=' | ')
    if (i + 1) % 5 == 0:
        print()

0 = 2022-05-26 | 1 = 2022-06-30 | 2 = 2022-07-28 | 3 = 2022-08-25 | 4 = 2022-09-29 | 
5 = 2022-10-27 | 6 = 2022-11-24 | 7 = 2022-12-29 | 8 = 2023-01-25 | 9 = 2023-02-23 | 
10 = 2023-03-29 | 11 = 2023-04-27 | 12 = 2023-05-25 | 13 = 2023-06-28 | 14 = 2023-06-29 | 
15 = 2023-07-27 | 16 = 2023-08-31 | 17 = 2023-09-28 | 18 = 2023-10-26 | 19 = 2023-11-30 | 
20 = 2023-12-28 | 21 = 2024-01-25 | 22 = 2024-02-29 | 23 = 2024-03-27 | 24 = 2024-04-24 | 
25 = 2024-05-29 | 26 = 2024-06-26 | 27 = 2024-07-31 | 

In [149]:
index = 20

expiry_date = expiry_future.iloc[index]['expiry']
# Fetch the futures data for the selected expiry date
nft = fetch_futures(cursor, symbol, expiry_date)
# Convert the 'date_timestamp' column to datetime if it exists
nft = nft.drop(columns=['id'])
nft = nft.drop_duplicates()



In [150]:
nft

symbol      date_timestamp     open      low     high    close  \
0      BANKNIFTY 2023-12-01 09:15:00  4479145  4476270  4483685  4482335   
2      BANKNIFTY 2023-12-01 09:16:00  4482165  4478740  4482625  4482285   
4      BANKNIFTY 2023-12-01 09:17:00  4482795  4481350  4483715  4483200   
6      BANKNIFTY 2023-12-01 09:18:00  4483240  4483240  4486500  4486500   
8      BANKNIFTY 2023-12-01 09:19:00  4486430  4485600  4487500  4486620   
...          ...                 ...      ...      ...      ...      ...   
14240  BANKNIFTY 2023-12-28 15:25:00  4850775  4850370  4851095  4850655   
14242  BANKNIFTY 2023-12-28 15:26:00  4850655  4850530  4851405  4851100   
14244  BANKNIFTY 2023-12-28 15:27:00  4851100  4850700  4851300  4851015   
14246  BANKNIFTY 2023-12-28 15:28:00  4851005  4851005  4851645  4851625   
14248  BANKNIFTY 2023-12-28 15:29:00  4851625  4850400  4851645  4851500   

       volume              expiry expiry_type  
0       48975 2023-12-28 14:30:00           I  
2       29175 2023-12-28 14:30:00           I  
4       27660 2023-12-28 14:30:00           I  
6       23925 2023-12-28 14:30:00           I  
8       15240 2023-12-28 14:30:00           I  
...       ...                 ...         ...  
14240    8535 2023-12-28 14:30:00           I  
14242    5400 2023-12-28 14:30:00           I  
14244    2130 2023-12-28 14:30:00           I  
14246    8220 2023-12-28 14:30:00           I  
14248    8085 2023-12-28 14:30:00           I  

[7125 rows x 9 columns]

In [151]:
print(type(nft.iloc[0]['date_timestamp']))

<class 'pandas._libs.tslibs.timestamps.Timestamp'>


In [152]:

# Generate the full range of timestamps for each day
start_time = '09:15:00'
end_time = '15:30:00'

all_timestamps = pd.date_range(start=start_time, end=end_time, freq='min').time

# Generate a DataFrame with all timestamps for each day in the data
all_dates = nft['date_timestamp'].dt.date.unique()
all_date_times = [pd.Timestamp.combine(date, time) for date in all_dates for time in all_timestamps]
all_date_times_df = pd.DataFrame(all_date_times, columns=['date_timestamp'])


# Merge with the original DataFrame to include all timestamps
nft_full = pd.merge(all_date_times_df, nft, on='date_timestamp', how='left')

for i in nft_full.iterrows():
    print(i[1])


# Forward fill missing values
nft_full = nft_full.ffill()

# Sort by date_timestamp to maintain order
nft_full = nft_full.sort_values('date_timestamp').reset_index(drop=True)



date_timestamp    2023-12-01 09:15:00
symbol                      BANKNIFTY
open                        4479145.0
low                         4476270.0
high                        4483685.0
close                       4482335.0
volume                        48975.0
expiry            2023-12-28 14:30:00
expiry_type                         I
Name: 0, dtype: object
date_timestamp    2023-12-01 09:16:00
symbol                      BANKNIFTY
open                        4482165.0
low                         4478740.0
high                        4482625.0
close                       4482285.0
volume                        29175.0
expiry            2023-12-28 14:30:00
expiry_type                         I
Name: 1, dtype: object
date_timestamp    2023-12-01 09:17:00
symbol                      BANKNIFTY
open                        4482795.0
low                         4481350.0
high                        4483715.0
close                       4483200.0
volume                        27660.0
expi

In [153]:

short_window = 9
long_window = 26
nft['Short_EMA'] = nft['close'].ewm(span=short_window, adjust=False).mean()
nft['Long_EMA'] = nft['close'].ewm(span=long_window, adjust=False).mean()

nft['Signal'] = 0 



In [154]:
for i in range(1, len(nft)):
    if nft['Short_EMA'].iloc[i] > nft['Long_EMA'].iloc[i] and nft['Short_EMA'].iloc[i-1] <= nft['Long_EMA'].iloc[i-1]:
        nft.at[nft.index[i], 'Signal'] = 1  # Buy signal
    elif nft['Short_EMA'].iloc[i] < nft['Long_EMA'].iloc[i] and nft['Short_EMA'].iloc[i-1] >= nft['Long_EMA'].iloc[i-1]:
        nft.at[nft.index[i], 'Signal'] = -1  # Sell signal

nft.head()

symbol      date_timestamp     open      low     high    close  volume  \
0  BANKNIFTY 2023-12-01 09:15:00  4479145  4476270  4483685  4482335   48975   
2  BANKNIFTY 2023-12-01 09:16:00  4482165  4478740  4482625  4482285   29175   
4  BANKNIFTY 2023-12-01 09:17:00  4482795  4481350  4483715  4483200   27660   
6  BANKNIFTY 2023-12-01 09:18:00  4483240  4483240  4486500  4486500   23925   
8  BANKNIFTY 2023-12-01 09:19:00  4486430  4485600  4487500  4486620   15240   

               expiry expiry_type  Short_EMA      Long_EMA  Signal  
0 2023-12-28 14:30:00           I  4482335.0  4.482335e+06       0  
2 2023-12-28 14:30:00           I  4482325.0  4.482331e+06      -1  
4 2023-12-28 14:30:00           I  4482500.0  4.482396e+06       1  
6 2023-12-28 14:30:00           I  4483300.0  4.482700e+06       0  
8 2023-12-28 14:30:00           I  4483964.0  4.482990e+06       0

In [155]:
t = nft[nft['Signal']!=0]

print(len(t))

284


In [156]:

fig = make_subplots(rows=1, cols=1)

# Candlestick chart
candlestick = go.Candlestick(
    x=nft.index,
    open=nft['open'],
    high=nft['high'],
    low=nft['low'],
    close=nft['close'],
    name='Candlesticks'
)
fig.add_trace(candlestick)

# Short EMA
short_ema = go.Scatter(x=nft.index, y=nft['Short_EMA'], mode='lines', name='Short EMA')
fig.add_trace(short_ema)

# Long EMA
long_ema = go.Scatter(x=nft.index, y=nft['Long_EMA'], mode='lines', name='Long EMA')
fig.add_trace(long_ema)

# Buy signals
buy_signals = go.Scatter(
    x=nft[nft['Signal'] == 1].index,
    y=nft['Short_EMA'][nft['Signal'] == 1],
    mode='markers',
    marker=dict(symbol='triangle-up', color='yellow', size=12),
    name='Buy Signal'
)
fig.add_trace(buy_signals)

# Sell signals
sell_signals = go.Scatter(
    x=nft[nft['Signal'] == -1].index,
    y=nft['Short_EMA'][nft['Signal'] == -1],
    mode='markers',
    marker=dict(symbol='triangle-down', color='black', size=12),
    name='Sell Signal'
)
fig.add_trace(sell_signals)

fig.update_layout(
    title=f'{symbol} EMA Crossover Strategy',
    yaxis_title='Price',
    xaxis_title='Date',
    xaxis_rangeslider_visible=False,
    width=2000,
    height=1000
)

# Save the plot as an HTML file
fig.show()
# pyo.plot(fig, filename='candlestick_chart.html', auto_open=True)

In [157]:
import plotly.graph_objs as go
from plotly.subplots import make_subplots
import plotly.offline as pyo

# Assuming 'nft' is already defined as your DataFrame
# Ensure 'date_timestamp' is in datetime format
nft['date_timestamp'] = pd.to_datetime(nft['date_timestamp'])

fig = make_subplots(rows=1, cols=1)

# Candlestick chart
candlestick = go.Candlestick(
    x=nft['date_timestamp'],
    open=nft['open'],
    high=nft['high'],
    low=nft['low'],
    close=nft['close'],
    name='Candlesticks'
)
fig.add_trace(candlestick)

# Short EMA
short_ema = go.Scatter(x=nft['date_timestamp'], y=nft['Short_EMA'], mode='lines', name='Short EMA')
fig.add_trace(short_ema)

# Long EMA
long_ema = go.Scatter(x=nft['date_timestamp'], y=nft['Long_EMA'], mode='lines', name='Long EMA')
fig.add_trace(long_ema)

# Buy signals
buy_signals = go.Scatter(
    x=nft[nft['Signal'] == 1]['date_timestamp'],
    y=nft['Short_EMA'][nft['Signal'] == 1],
    mode='markers',
    marker=dict(symbol='triangle-up', color='yellow', size=12),
    name='Buy Signal'
)
fig.add_trace(buy_signals)

# Sell signals
sell_signals = go.Scatter(
    x=nft[nft['Signal'] == -1]['date_timestamp'],
    y=nft['Short_EMA'][nft['Signal'] == -1],
    mode='markers',
    marker=dict(symbol='triangle-down', color='black', size=12),
    name='Sell Signal'
)
fig.add_trace(sell_signals)

fig.update_layout(
    title=f'{symbol} EMA Crossover Strategy',
    yaxis_title='Price',
    xaxis_title='Date',
    xaxis_rangeslider_visible=False,
    width=2000,
    height=1000
)

# Save the plot as an HTML file
pyo.plot(fig, filename='candlestick_chart.html', auto_open=True)


'candlestick_chart.html'

In [158]:

position_size = 1  
current_position = 0  # Track current position (1 for long, -1 for short, 0 for neutral)
entry_price = 0  # Track entry price
total_pnl = 0  # Total P&L
# Iterate through each row in the DataFrame
for index, row in nft.iterrows():
    if row['Signal'] == 1 and current_position == 0:  # Buy signal and no current position
        current_position = 1
        # print("entry")
        entry_price = row['close']
    elif row['Signal'] == -1 and current_position == 1:  # Sell signal and long position
        pnl = (row['close'] - entry_price) * position_size
        total_pnl += pnl
        current_position = 0
        entry_price = 0
    elif row['Signal'] == -1 and current_position == 0:  # Sell signal but no current long position
        continue  # Can't sell if not long

# Print total P&L
print(f'Total P&L: {total_pnl}')

Total P&L: 256635


In [159]:

cursor1 = conn.cursor()
options = fetch_options(cursor1, symbol=symbol, expiry=str(expiry_date))

options.drop(columns=['id'],inplace = True)
options.drop_duplicates(inplace=True)

In [160]:
copt = options[options['opt_type']=='CE'].copy()
popt = options[options['opt_type']=='PE'].copy()
print(len(copt),len(popt))
ce.drop_duplicates(inplace = True)
popt.drop_duplicates(inplace = True)
print(len(ce),len(popt))


314782 431655
912000 431655


In [161]:

strike_values = options['strike'].unique()
all_timestamps = options['date_timestamp'].unique()

d2c = [[j, i]  for j in all_timestamps for i in strike_values]

d2c_df = pd.DataFrame(d2c , columns = ['date_timestamp' , 'strike'])

In [162]:
ce = pd.merge(d2c_df , copt,on=['date_timestamp','strike'] , how='left')
pe = pd.merge(d2c_df , popt,on=['date_timestamp','strike'] , how='left')

ce = ce.ffill().bfill()
pe = pe.ffill().bfill()

In [163]:
ce.to_csv('ce.csv')
pe.to_csv('pe.csv')

In [164]:
def binary_search(arr, target):
    low , high = 0, len(arr)
    while low < high:
        mid = low + (high -low)//2
        if arr['strike'].iloc[mid] < target:
            low = mid + 1
        else:
            high = mid
    return low


In [165]:
# Define the structures
put = {'pos': 0, 'signal_time': None, 'long_ema': None, 'short_ema': None, 'entry_time': None, 'strike': None,
        'entry_price': None, 'exit_time': None, 'exit_price': None , 'pnl': 0 ,'type':None, 'pnl_sum':0 , 'price':None}
call = {'pos': 0, 'signal_time': None, 'long_ema': None, 'short_ema': None, 'entry_time': None, 'strike': None,
         'entry_price': None, 'exit_time': None, 'exit_price': None , 'pnl': 0 ,'type':None, 'pnl_sum':0 , 'price':None}

# Initialize trades list
trades = []
pnl = []
per_trade_data = []
for i in range(len(nft) - 1):
    row = nft.iloc[i]
    signal = row['Signal']
    price_selector = 1
    price = nft.iloc[i + 1]['close'] if price_selector == 1 else nft.iloc[i + 1]['open']
    dt = nft.iloc[i + 1]['date_timestamp']

    if signal == 1:
        if call['pos'] == 0:
            strikes = ce[ce['date_timestamp'] == dt][['date_timestamp', 'open', 'strike']]
            if not strikes.empty:
                strikes.sort_values(by='strike', inplace=True)
                var = price
                strikes.reset_index(drop=True, inplace=True)
                index = binary_search(strikes, var)
                if index >= len(strikes):
                    index -= 1
                if index > 0:
                    index -= 1
                buy_val = strikes['open'].iloc[index]
                call.update({'pos': 1, 'price': row['close'], 'signal_time': row['date_timestamp'], 'long_ema': row['Long_EMA'],
                             'short_ema': row['Short_EMA'], 'strike': strikes['strike'].iloc[index],
                             'entry_time': dt, 'entry_price': buy_val})
            else:
                print(f'No strikes on call option at {i} and {dt}')
        if put['pos'] == 1:
            strikes = pe[(pe['date_timestamp'] == dt) & (pe['strike'] == put['strike'])]
            if not strikes.empty:
                var = strikes['open'].iloc[0]
                put.update({'pos': 0, 'exit_time': dt, 'exit_price': var, 'pnl': var - put['entry_price'], 'type': 'PE'})
                trades.append(put.copy())
            else:
                print(f'No closing on put option at {i}, {dt}, {put["strike"]}')

    elif signal == -1:
        if put['pos'] == 0:
            strikes = pe[pe['date_timestamp'] == dt][['date_timestamp', 'open', 'strike']]
            if not strikes.empty:
                strikes.sort_values(by='strike', inplace=True)
                var = price
                strikes.reset_index(drop=True, inplace=True)
                index = binary_search(strikes, var)
                if index >= len(strikes):
                    index -= 1
                if index < len(strikes):
                    index += 1
                sell_val = strikes['open'].iloc[index]
                put.update({'pos': 1, 'price': row['close'], 'signal_time': row['date_timestamp'], 'long_ema': row['Long_EMA'],
                            'short_ema': row['Short_EMA'], 'strike': strikes['strike'].iloc[index],
                            'entry_time': dt, 'entry_price': sell_val})
            else:
                print(f'No strikes on put option at {i} and {dt}')
        if call['pos'] == 1:
            strikes = ce[(ce['date_timestamp'] == dt) & (ce['strike'] == call['strike'])]
            if not strikes.empty:
                var = strikes['open'].iloc[0]
                call.update({'pos': 0, 'exit_time': dt, 'exit_price': var, 'pnl': var - call['entry_price'], 'type': 'CE'})
                trades.append(call.copy())
            else:
                print(f'No closing on call option at {i}, {dt}, {call["strike"]}')

# Final closing for any open positions at the end of the dataset
if call['pos'] == 1:
    call_short = ce[(ce['date_timestamp'] == nft.iloc[-1]['date_timestamp']) & (ce['strike'] == call['strike'])]
    if not call_short.empty:
        var = call_short.iloc[0]['close']
        call.update({'pos': 0, 'exit_time': nft.iloc[-1]['date_timestamp'], 'exit_price': var, 'pnl': var - call['entry_price']})
        trades.append(call.copy())
    else:
        print('No closing on call option')

if put['pos'] == 1:
    put_short = pe[(pe['date_timestamp'] == nft.iloc[-1]['date_timestamp']) & (pe['strike'] == put['strike'])]
    if not put_short.empty:
        var = put_short.iloc[0]['close']
        put.update({'pos': 0, 'exit_time': nft.iloc[-1]['date_timestamp'], 'exit_price': var, 'pnl': var - put['entry_price']})
        trades.append(put.copy())
    else:
        print('No closing on put option')

In [166]:
print(put['pos'],call['pos'])

0 0


In [167]:
for i in range(1,len(trades)):
    trades[i]['pnl_sum'] = trades[i-1]['pnl_sum'] + trades[i]['pnl']

In [168]:
fig = go.Figure()

fig.add_trace(go.Scatter(
    x=[i for i in range(len(trades))],
    y=[i['pnl'] for i in trades],
    mode='lines+markers',
    name='PnL'
))

fig.show()

In [169]:
fig = go.Figure()

fig.add_trace(go.Scatter(
    x=[i for i in range(len(trades))],
    y=[i['pnl_sum'] for i in trades],
    mode='lines+markers',
    name='PnL'
))

fig.show()

In [170]:
def drawdown(arr):
    max_val = -10000000000
    max_index , i = 0 , 0
    drawdown_val = -10000000000
    while i < len(arr):
        if arr[i]['pnl_sum'] > max_val:
            max_val = arr[i]['pnl_sum']
            while i < len(arr) and arr[i]['pnl_sum']<=max_val:
                drawdown_val = max(drawdown_val, max_val - arr[i]['pnl_sum'])
                i += 1

    return drawdown_val


In [171]:
drawdownval = drawdown(trades)
print(drawdownval)

197565.0


In [172]:
for i in trades:
    print(f" signal time {i['signal_time']} | price {i['price']} |  on date_time {i['entry_time']} | strike {i['strike']} | type : {i['type']}|  buy price {i['entry_price']}  |   sold at {i['exit_price']} on {i['exit_time']} , short_ema {i['short_ema']} | long_ema {i['long_ema']} |  PnL = {i['pnl']}")

 signal time 2023-12-01 09:16:00 | price 4482285 |  on date_time 2023-12-01 09:17:00 | strike 4500000 | type : PE|  buy price 67500.0  |   sold at 67000.0 on 2023-12-01 09:18:00 , short_ema 4482325.0 | long_ema 4482331.296296297 |  PnL = -500.0
 signal time 2023-12-01 09:17:00 | price 4483200 |  on date_time 2023-12-01 09:18:00 | strike 4480000 | type : CE|  buy price 62300.0  |   sold at 79750.0 on 2023-12-01 10:38:00 , short_ema 4482500.0 | long_ema 4482395.644718793 |  PnL = 17450.0
 signal time 2023-12-01 10:37:00 | price 4511600 |  on date_time 2023-12-01 10:38:00 | strike 4530000 | type : PE|  buy price 2955.0  |   sold at 67560.0 on 2023-12-01 10:39:00 , short_ema 4512317.106309336 | long_ema 4512325.156835257 |  PnL = 64605.0
 signal time 2023-12-01 10:38:00 | price 4512700 |  on date_time 2023-12-01 10:39:00 | strike 4510000 | type : CE|  buy price 62850.0  |   sold at 61080.0 on 2023-12-01 10:43:00 , short_ema 4512393.685047468 | long_ema 4512352.922995608 |  PnL = -1770.0
 s

In [173]:
pnl_per_day = {}

for trade in trades:
    if trade['entry_time'] not in pnl_per_day:
        pnl_per_day[trade['entry_time']] = []
    pnl_per_day[trade['entry_time']].append(-trade['entry_price'])

    if trade['exit_time'] not in pnl_per_day:
        pnl_per_day[trade['exit_time']] = []
    pnl_per_day[trade['exit_time']].append(trade['exit_price'])


net_pnl_per_day = {}

for day in pnl_per_day:

    net_pnl_per_day[day] = sum(pnl_per_day[day])
    

In [174]:
entry_per_day = {}
exit_per_day = {}

for trade in trades:
    if trade['entry_time'] not in entry_per_day:
        entry_per_day[trade['entry_time']] = 0.0
    entry_per_day[trade['entry_time']] += trade['entry_price']

    if trade['exit_time'] not in exit_per_day:
        exit_per_day[trade['exit_time']] = 0.0
    exit_per_day[trade['exit_time']] += trade['exit_price']


In [175]:
percentage_pnl = {}

for day in entry_per_day:
    percentage_pnl[day] = (net_pnl_per_day[day] / entry_per_day[day]) * 100

In [176]:
arr = np.array(list(percentage_pnl.values()))

mean = np.mean(arr)

std_dev = np.std(arr)

risk_free_rate = 0.0

sharpe_ratio = (mean - risk_free_rate) / std_dev

print(sharpe_ratio)

0.10466410139763432
